In [52]:
%load_ext autoreload
%autoreload 2
%env ANYWIDGET_HMR=1
%load_ext rpy2.ipython

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload
env: ANYWIDGET_HMR=1
The rpy2.ipython extension is already loaded. To reload it, use:
  %reload_ext rpy2.ipython


In [53]:
from surprise_explora import Widget

w = Widget()

## Create Dataframe

Create a dataframe with fips, group's population, and rates

In [54]:
%%R -o poverty_data
#Install packages
install.packages('tidycensus')

#load packages
library(tidycensus)
library(dplyr)
library(tidyr)
library(stringr)

#Set API Key
Sys.setenv(CENSUS_KEY="f7332e69229418824c5765d1baad389fdb9b923c")

# Target variables
poverty_vars <- c(
  white_total    = "B17001A_001",  # Total White population
  white_poverty  = "B17001A_002",  # White population below poverty
  black_total    = "B17001B_001",  # Total Black population
  black_poverty  = "B17001B_002",  # Black population below poverty
  hispanic_total    = "B17001I_001",  # Total Hispanic population
  hispanic_poverty  = "B17001I_002",   # Hispanic population below poverty
  county_total = "B17001_001", # Total County Population
  county_poverty = "B17001_002" # Total County Poverty
)

# Retrieve county-level data
poverty_data <- get_acs(
  geography = "county",
  variables = poverty_vars,
  year = 2021,
  survey = "acs5",
  output    = "wide"
)


The downloaded binary packages are in
	/var/folders/fr/sw6vgkr93zn67yqw2mnd3dvw0000gr/T//RtmpQjpyRT/downloaded_packages


trying URL 'https://repo.miserver.it.umich.edu/cran/bin/macosx/big-sur-arm64/contrib/4.4/tidycensus_1.7.1.tgz'
Content type 'application/octet-stream' length 3554938 bytes (3.4 MB)
downloaded 3.4 MB

Getting data from the 2017-2021 5-year ACS


In [55]:
import pandas as pd

poverty_data_by_race = poverty_data.copy()

poverty_data_by_race["poverty_rate_white"]   = (poverty_data_by_race["white_povertyE"]   / poverty_data_by_race["white_totalE"])   * 100
poverty_data_by_race["poverty_rate_black"]   = (poverty_data_by_race["black_povertyE"]   / poverty_data_by_race["black_totalE"])   * 100
poverty_data_by_race["poverty_rate_hispanic"] = (poverty_data_by_race["hispanic_povertyE"] / poverty_data_by_race["hispanic_totalE"]) * 100
poverty_data_by_race["poverty_rate_all"]     = (poverty_data_by_race["county_povertyE"]  / poverty_data_by_race["county_totalE"]) * 100 

poverty_data_by_race = poverty_data_by_race.rename(columns={
    "white_totalE":    "population_white",
    "black_totalE":    "population_black",
    "hispanic_totalE": "population_hispanic",
    "county_totalE":   "population_all"
})

df = poverty_data_by_race[[
    "GEOID",                    
    "NAME",
    "poverty_rate_black",
    "population_black",
    "poverty_rate_white",
    "population_white",
    "poverty_rate_hispanic",
    "population_hispanic",
    "poverty_rate_all",
    "population_all"
]].rename(columns={"GEOID": "fips"})

county_typology = pd.read_csv('data/county_typology.csv', dtype=str)

df = pd.merge(df, county_typology, on='fips', how='left').dropna()
df 

fips                        NAME  poverty_rate_black  population_black  \
0     01001     Autauga County, Alabama           24.573589           11374.0   
1     01003     Baldwin County, Alabama           20.576692           19109.0   
2     01005     Barbour County, Alabama           36.152797           10262.0   
3     01007        Bibb County, Alabama           33.695652            4232.0   
4     01009      Blount County, Alabama           23.349436             621.0   
...     ...                         ...                 ...               ...   
3137  56035    Sublette County, Wyoming          100.000000               1.0   
3138  56037  Sweetwater County, Wyoming           19.628099             484.0   
3139  56039       Teton County, Wyoming           17.469880             166.0   
3140  56041       Uinta County, Wyoming            2.000000              50.0   
3142  56045      Weston County, Wyoming          100.000000              16.0   

      poverty_rate_white  population_white  poverty_rate_hispanic  \
0              10.286056           43418.0              13.597734   
1               7.522396          190099.0              18.329028   
2              14.060850           10419.0              60.356789   
3              12.979423           16426.0              13.764511   
4              12.741977           54034.0              25.808180   
...                  ...               ...                    ...   
3137            8.138846            8441.0              28.393136   
3138           10.184015           36410.0              17.103712   
3139            6.021299           19813.0              11.497557   
3140            6.495177           18660.0              27.380340   
3142           13.681850            5796.0              35.897436   

      population_hispanic  poverty_rate_all  population_all  \
0                  1765.0         13.578474         57790.0   
1                 10066.0          9.204905        223772.0   
2                  1009.0         26.471910         22250.0   
3                   603.0         16.942857         21000.0   
4                  5599.0         13.236630         58323.0   
...                   ...               ...             ...   
3137                641.0          8.302058          8793.0   
3138               6788.0         10.481391         41941.0   
3139               3479.0          7.117040         23240.0   
3140               1943.0          7.958751         20267.0   
3142                 78.0         14.085591          6496.0   

                    typology  
0      Working Class Country  
1       Rural Middle America  
2     African American South  
3           Evangelical Hubs  
4           Evangelical Hubs  
...                      ...  
3137         Aging Farmlands  
3138                  Exurbs  
3139                  Exurbs  
3140    Rural Middle America  
3142         Aging Farmlands  

[2942 rows x 11 columns]

In [56]:
df['state'] = df['NAME'].str.split(', ').str[1].str.strip()

df["name"] = df["NAME"].str.split(", ").str[0]

df['white_pop'] = df['population_white']
df['black_pop'] = df['population_black']
df['hispanic_pop'] = df['population_hispanic']
df['global_rate'] = df['poverty_rate_all'] / 100
df['global_pop'] = df['population_all']


df['white_rate'] = df['poverty_rate_white'] / 100
df['black_rate'] = df['poverty_rate_black'] / 100
df['hispanic_rate'] = df['poverty_rate_hispanic'] / 100
df = df.drop(columns=['population_white', 'population_black', 'population_hispanic', 'poverty_rate_all', 'population_all', 'poverty_rate_white', 'poverty_rate_black', 'poverty_rate_hispanic'])

In [57]:
df

fips                        NAME                typology    state  \
0     01001     Autauga County, Alabama   Working Class Country  Alabama   
1     01003     Baldwin County, Alabama    Rural Middle America  Alabama   
2     01005     Barbour County, Alabama  African American South  Alabama   
3     01007        Bibb County, Alabama        Evangelical Hubs  Alabama   
4     01009      Blount County, Alabama        Evangelical Hubs  Alabama   
...     ...                         ...                     ...      ...   
3137  56035    Sublette County, Wyoming         Aging Farmlands  Wyoming   
3138  56037  Sweetwater County, Wyoming                  Exurbs  Wyoming   
3139  56039       Teton County, Wyoming                  Exurbs  Wyoming   
3140  56041       Uinta County, Wyoming    Rural Middle America  Wyoming   
3142  56045      Weston County, Wyoming         Aging Farmlands  Wyoming   

                   name  white_pop  black_pop  hispanic_pop  global_rate  \
0        Autauga County    43418.0    11374.0        1765.0     0.135785   
1        Baldwin County   190099.0    19109.0       10066.0     0.092049   
2        Barbour County    10419.0    10262.0        1009.0     0.264719   
3           Bibb County    16426.0     4232.0         603.0     0.169429   
4         Blount County    54034.0      621.0        5599.0     0.132366   
...                 ...        ...        ...           ...          ...   
3137    Sublette County     8441.0        1.0         641.0     0.083021   
3138  Sweetwater County    36410.0      484.0        6788.0     0.104814   
3139       Teton County    19813.0      166.0        3479.0     0.071170   
3140       Uinta County    18660.0       50.0        1943.0     0.079588   
3142      Weston County     5796.0       16.0          78.0     0.140856   

      global_pop  white_rate  black_rate  hispanic_rate  
0        57790.0    0.102861    0.245736       0.135977  
1       223772.0    0.075224    0.205767       0.183290  
2        22250.0    0.140609    0.361528       0.603568  
3        21000.0    0.129794    0.336957       0.137645  
4        58323.0    0.127420    0.233494       0.258082  
...          ...         ...         ...            ...  
3137      8793.0    0.081388    1.000000       0.283931  
3138     41941.0    0.101840    0.196281       0.171037  
3139     23240.0    0.060213    0.174699       0.114976  
3140     20267.0    0.064952    0.020000       0.273803  
3142      6496.0    0.136818    1.000000       0.358974  

[2942 rows x 13 columns]

## Setup Suprise

Create surprise object by adding groups we are interested in.

Then calculate surprise for each fo those groups.

In [58]:
#Filter out an individual county 
county_list = ['06037'] 
df_filtered = df[~df["fips"].isin(county_list)]

#Filter by population range
df_filtered = df[(df['global_pop'] > 100000) & (df['global_pop'] < 200000)]
#df_filtered = surprise.df[(surprise.df['white_pop'] > 100000) & (surprise.df['white_pop'] < 200000)]
#df_filtered = surprise.df[(surprise.df['black_pop'] > 100000) & (surprise.df['black_pop'] < 200000)]
#df_filtered = surprise.df[(surprise.df['hispanic_pop'] > 100000) & (surprise.df['hispanic_pop'] < 200000)]

#Filter by typology - comment out typology
typology = [
'Working Class Country', 
'Rural Middle America', 
'African American South', 
#'Evangelical Hubs'
#'Military Posts',
#'College Towns',
#'Exurbs',
#'Native American Lands',
#'Graying America',
#'Hispanic Centers',
#'Big Cities',
#'Urban Suburbs',
#'Aging Farmlands',
#'Middle Suburbs',
#'LDS Enclaves',
]
df_filtered = df[df["typology"].isin(typology)]

df_filtered

fips                     NAME                typology    state  \
0     01001  Autauga County, Alabama   Working Class Country  Alabama   
1     01003  Baldwin County, Alabama    Rural Middle America  Alabama   
2     01005  Barbour County, Alabama  African American South  Alabama   
5     01011  Bullock County, Alabama  African American South  Alabama   
6     01013   Butler County, Alabama  African American South  Alabama   
...     ...                      ...                     ...      ...   
3127  56015   Goshen County, Wyoming    Rural Middle America  Wyoming   
3131  56023  Lincoln County, Wyoming    Rural Middle America  Wyoming   
3132  56025  Natrona County, Wyoming    Rural Middle America  Wyoming   
3134  56029     Park County, Wyoming    Rural Middle America  Wyoming   
3140  56041    Uinta County, Wyoming    Rural Middle America  Wyoming   

                name  white_pop  black_pop  hispanic_pop  global_rate  \
0     Autauga County    43418.0    11374.0        1765.0     0.135785   
1     Baldwin County   190099.0    19109.0       10066.0     0.092049   
2     Barbour County    10419.0    10262.0        1009.0     0.264719   
5     Bullock County     2442.0     6840.0         880.0     0.309346   
6      Butler County     9661.0     8537.0         308.0     0.181770   
...              ...        ...        ...           ...          ...   
3127   Goshen County    10677.0       54.0        1290.0     0.080540   
3131  Lincoln County    18365.0       11.0         939.0     0.067139   
3132  Natrona County    71680.0      542.0        6922.0     0.098777   
3134     Park County    27128.0      189.0        1649.0     0.086003   
3140    Uinta County    18660.0       50.0        1943.0     0.079588   

      global_pop  white_rate  black_rate  hispanic_rate  
0        57790.0    0.102861    0.245736       0.135977  
1       223772.0    0.075224    0.205767       0.183290  
2        22250.0    0.140609    0.361528       0.603568  
5         9908.0    0.192875    0.360526       0.540909  
6        18870.0    0.096574    0.271407       0.266234  
...          ...         ...         ...            ...  
3127     11783.0    0.081858    0.000000       0.043411  
3131     19333.0    0.062129    0.000000       0.121406  
3132     77680.0    0.096317    0.387454       0.156747  
3134     29150.0    0.078111    0.592593       0.229230  
3140     20267.0    0.064952    0.020000       0.273803  

[1157 rows x 13 columns]

In [59]:
from surprise_explora import Surprise

groups = ['white', 'black', 'hispanic']
rate_keys = ['white_rate', 'black_rate', 'hispanic_rate']
population_keys = ['white_pop', 'black_pop', 'hispanic_pop']
global_rate_key = 'global_rate'
global_population_key = 'global_pop'

surprise = Surprise(
    df=df_filtered,
    groups=groups, 
    rate_keys=rate_keys,
    population_keys=population_keys,
    global_rate_key=global_rate_key,
    global_population_key=global_population_key
)

# Calculate surprise for each group
surprise.calculate()

/Users/andlovu/Documents/GitHub/surprise-explora/src/surprise_explora/__init__.py:65: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.df[self.name + "_zScore"] = self.zScore
/Users/andlovu/Documents/GitHub/surprise-explora/src/surprise_explora/__init__.py:68: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.df[self.name + "_surprise"] = self.surprise
/Users/andlovu/Documents/GitHub/surprise-explora/src/surprise_explora/__init__.py:65: SettingWithCopyWarning: 
A value is trying to be set on a copy of a 

In [60]:
# Dataframe with surprise values for each group
surprise.df

fips                     NAME                typology    state  \
0     01001  Autauga County, Alabama   Working Class Country  Alabama   
1     01003  Baldwin County, Alabama    Rural Middle America  Alabama   
2     01005  Barbour County, Alabama  African American South  Alabama   
5     01011  Bullock County, Alabama  African American South  Alabama   
6     01013   Butler County, Alabama  African American South  Alabama   
...     ...                      ...                     ...      ...   
3127  56015   Goshen County, Wyoming    Rural Middle America  Wyoming   
3131  56023  Lincoln County, Wyoming    Rural Middle America  Wyoming   
3132  56025  Natrona County, Wyoming    Rural Middle America  Wyoming   
3134  56029     Park County, Wyoming    Rural Middle America  Wyoming   
3140  56041    Uinta County, Wyoming    Rural Middle America  Wyoming   

                name  white_pop  black_pop  hispanic_pop  global_rate  \
0     Autauga County    43418.0    11374.0        1765.0     0.135785   
1     Baldwin County   190099.0    19109.0       10066.0     0.092049   
2     Barbour County    10419.0    10262.0        1009.0     0.264719   
5     Bullock County     2442.0     6840.0         880.0     0.309346   
6      Butler County     9661.0     8537.0         308.0     0.181770   
...              ...        ...        ...           ...          ...   
3127   Goshen County    10677.0       54.0        1290.0     0.080540   
3131  Lincoln County    18365.0       11.0         939.0     0.067139   
3132  Natrona County    71680.0      542.0        6922.0     0.098777   
3134     Park County    27128.0      189.0        1649.0     0.086003   
3140    Uinta County    18660.0       50.0        1943.0     0.079588   

      global_pop  ...  black_rate  hispanic_rate  white_zScore  \
0        57790.0  ...    0.245736       0.135977     -0.492491   
1       223772.0  ...    0.205767       0.183290     -1.194856   
2        22250.0  ...    0.361528       0.603568      0.466846   
5         9908.0  ...    0.360526       0.540909      1.795155   
6        18870.0  ...    0.271407       0.266234     -0.652264   
...          ...  ...         ...            ...           ...   
3127     11783.0  ...    0.000000       0.043411     -1.026252   
3131     19333.0  ...    0.000000       0.121406     -1.527655   
3132     77680.0  ...    0.387454       0.156747     -0.658793   
3134     29150.0  ...    0.592593       0.229230     -1.121480   
3140     20267.0  ...    0.020000       0.273803     -1.455917   

      white_surprise  black_zScore  black_surprise  hispanic_zScore  \
0          -0.019659     -0.202839       -0.009060        -0.533520   
1          -0.096797     -0.412470       -0.023754        -0.256368   
2           0.009163      0.404471        0.017111         2.205552   
5           0.017011      0.399218        0.013805         1.838506   
6          -0.012314     -0.068200       -0.002645         0.229502   
...              ...           ...             ...              ...   
3127       -0.020310     -1.491684        0.000000        -1.075760   
3131       -0.039372     -1.491684        0.000000        -0.618878   
3132       -0.033617      0.540448        0.005277        -0.411857   
3134       -0.035184      1.616368        0.009306         0.012738   
3140       -0.037845     -1.386787       -0.004114         0.273843   

      hispanic_surprise  global_zScore  global_surprise  
0             -0.016328      -0.258065        -0.010445  
1             -0.018721      -0.975773        -0.075793  
2              0.050389       1.857764         0.046044  
5              0.039392       2.590097         0.042890  
6              0.002948       0.496559         0.011480  
...                 ...            ...              ...  
3127          -0.028026      -1.164642        -0.021202  
3131          -0.013827      -1.384549        -0.032156  
3132          -0.024884      -0.865366        -0.040165  
3134           0.000379    

In [61]:
chart =  surprise.bar_chart(state='Alabama')

In [62]:
chart

alt.FacetChart(...)

In [63]:
import altair as alt
import numpy as np 

# GLOBAL

global_filtered = df_filtered.copy()

rate_mean = global_filtered['global_rate'].mean()
std_dev = global_filtered['global_rate'].std()
totalPop = global_filtered['global_pop'].sum()


global_filtered['n'] = global_filtered['global_pop'] / totalPop
global_filtered['ci'] = (1.96 * std_dev) / np.sqrt(global_filtered['n'])
global_filtered['lcl95'] = rate_mean - global_filtered['ci']
global_filtered['ucl95'] = rate_mean + global_filtered['ci']

maxzScore = max(abs(global_filtered['global_zScore']))
g_df = global_filtered[(global_filtered['lcl95'] > -(maxzScore)) & (global_filtered['ucl95'] < (maxzScore))]

max_surprise = global_filtered['global_surprise'].max()
min_surprise = global_filtered['global_surprise'].min()
abs_max = max(abs(max_surprise), abs(min_surprise))

# Lower confidence interval line
ci_lower = alt.Chart(g_df).mark_line(color='black').encode(
    x='global_pop',
    y='lcl95'
)

# Upper confidence interval line
ci_upper = alt.Chart(g_df).mark_line(color='black').encode(
    x='global_pop',
    y='ucl95'
)

chart = alt.Chart(global_filtered).mark_circle(size=60).encode(
    x='global_pop',
    y='global_zScore',
    color=alt.Color('global_surprise', scale=alt.Scale(scheme='redblue', domainMid=0, domain=[-abs_max, abs_max])),
    tooltip=['name', 'global_surprise']
).properties(
    width=800,
    height=400
)
chart + ci_lower + ci_upper 

alt.LayerChart(...)

In [64]:
# WHITE

white_filtered = df_filtered.copy()

rate_mean = white_filtered['white_rate'].mean()
std_dev = white_filtered['white_rate'].std()
totalPop = white_filtered['white_pop'].sum()


white_filtered['n'] = white_filtered['white_pop'] / totalPop
white_filtered['ci'] = (1.96 * std_dev) / np.sqrt(white_filtered['n'])
white_filtered['lcl95'] = rate_mean - white_filtered['ci']
white_filtered['ucl95'] = rate_mean + white_filtered['ci']

maxzScore = max(abs(white_filtered['white_zScore']))
w_df = white_filtered[(white_filtered['lcl95'] > -(maxzScore)) & (white_filtered['ucl95'] < (maxzScore))]

max_surprise = white_filtered['white_surprise'].max()
min_surprise = white_filtered['white_surprise'].min()
abs_max = max(abs(max_surprise), abs(min_surprise))

# Lower confidence interval line
ci_lower = alt.Chart(w_df).mark_line(color='black').encode(
    x='white_pop',
    y='lcl95'
)

# Upper confidence interval line
ci_upper = alt.Chart(w_df).mark_line(color='black').encode(
    x='white_pop',
    y='ucl95'
)

max_surprise = white_filtered['white_surprise'].max()
min_surprise = white_filtered['white_surprise'].min()
abs_max = max(abs(max_surprise), abs(min_surprise))

chart = alt.Chart(white_filtered).mark_circle(size=60).encode(
    x='white_pop',
    y='white_zScore',
    color=alt.Color('white_surprise', scale=alt.Scale(scheme='redblue', domainMid=0, domain=[-abs_max, abs_max])),
    tooltip=['name', 'white_surprise']
).properties(
    width=800,
    height=400
)
chart + ci_lower + ci_upper

alt.LayerChart(...)

In [65]:
# BLACK

black_filtered = df_filtered.copy()

rate_mean = black_filtered['black_rate'].mean()
std_dev = black_filtered['black_rate'].std()
totalPop = black_filtered['black_pop'].sum()


black_filtered['n'] = black_filtered['black_pop'] / totalPop
black_filtered['ci'] = (1.96 * std_dev) / np.sqrt(black_filtered['n'])
black_filtered['lcl95'] = rate_mean - black_filtered['ci']
black_filtered['ucl95'] = rate_mean + black_filtered['ci']

maxzScore = max(abs(black_filtered['black_zScore']))
b_df = black_filtered[(black_filtered['lcl95'] > -8) & (black_filtered['ucl95'] < 8)]

max_surprise = black_filtered['black_surprise'].max()
min_surprise = black_filtered['black_surprise'].min()
abs_max = max(abs(max_surprise), abs(min_surprise))

# Lower confidence interval line
ci_lower = alt.Chart(b_df).mark_line(color='black').encode(
    x='black_pop',
    y='lcl95'
)

# Upper confidence interval line
ci_upper = alt.Chart(b_df).mark_line(color='black').encode(
    x='black_pop',
    y='ucl95'
)

max_surprise = black_filtered['black_surprise'].max()
min_surprise = black_filtered['black_surprise'].min()
abs_max = max(abs(max_surprise), abs(min_surprise))

chart = alt.Chart(black_filtered).mark_circle(size=60).encode(
    x='black_pop',
    y='black_zScore',
    color=alt.Color('black_surprise', scale=alt.Scale(scheme='redblue', domainMid=0, domain=[-abs_max, abs_max])),
    tooltip=['name', 'black_surprise']
).properties(
    width=800,
    height=400
)
chart + ci_upper + ci_lower

alt.LayerChart(...)

In [66]:
# HISPANIC

hispanic_filtered = df_filtered.copy()

rate_mean = hispanic_filtered['hispanic_rate'].mean()
std_dev = hispanic_filtered['hispanic_rate'].std()
totalPop = hispanic_filtered['hispanic_pop'].sum()


hispanic_filtered['n'] = hispanic_filtered['hispanic_pop'] / totalPop
hispanic_filtered['ci'] = (1.96 * std_dev) / np.sqrt(hispanic_filtered['n'])
hispanic_filtered['lcl95'] = rate_mean - hispanic_filtered['ci']
hispanic_filtered['ucl95'] = rate_mean + hispanic_filtered['ci']

maxzScore = max(abs(hispanic_filtered['hispanic_zScore']))
h_df = hispanic_filtered[(hispanic_filtered['lcl95'] > -8) & (hispanic_filtered['ucl95'] < 8)]

max_surprise = hispanic_filtered['hispanic_surprise'].max()
min_surprise = hispanic_filtered['hispanic_surprise'].min()
abs_max = max(abs(max_surprise), abs(min_surprise))

# Lower confidence interval line
ci_lower = alt.Chart(h_df).mark_line(color='black').encode(
    x='hispanic_pop',
    y='lcl95'
)

# Upper confidence interval line
ci_upper = alt.Chart(h_df).mark_line(color='black').encode(
    x='hispanic_pop',
    y='ucl95'
)

max_surprise = hispanic_filtered['hispanic_surprise'].max()
min_surprise = hispanic_filtered['hispanic_surprise'].min()
abs_max = max(abs(max_surprise), abs(min_surprise))

max_surprise = hispanic_filtered['hispanic_surprise'].max()
min_surprise = hispanic_filtered['hispanic_surprise'].min()
abs_max = max(abs(max_surprise), abs(min_surprise))

chart = alt.Chart(hispanic_filtered).mark_circle(size=60).encode(
    x='hispanic_pop',
    y='hispanic_zScore',
    color=alt.Color('hispanic_surprise', scale=alt.Scale(scheme='redblue', domainMid=0, domain=[-abs_max, abs_max])),
    tooltip=['name', 'hispanic_surprise']
).properties(
    width=800,
    height=400
)
chart + ci_lower + ci_upper

alt.LayerChart(...)